# Week 6 Assignment

## Environment Review

In [1]:
import sys

sys.version

'3.6.10 |Anaconda, Inc.| (default, Mar 25 2020, 23:51:54) \n[GCC 7.3.0]'

In [4]:
%%bash

ls
echo ""
cd necessary_scripts/
ls
echo ""
echo "----------------------"
echo "Line Count of getMutations"
wc -l getMutations.py
echo ""
echo "----------------------"
echo "Line Count of parseFastq.py"
wc -l parseFastq.py

dgorgon_reference.fa
harrington_clinical_data.txt
hawkins_pooled_sequences.fastq
necessary_scripts
Week6_Lay_that_Pipe.ipynb

faker.sorted.bam
faker.sorted.bam.bai
getMutations.py
parseFastq.py

----------------------
Line Count of getMutations
29 getMutations.py

----------------------
Line Count of parseFastq.py
92 parseFastq.py


### Initial Thoughts

These files are just too big, to look cat them out above, let's bring these files into jupyter

### hawking_pooled_sequences.fastq

In [7]:
%%bash

head -10 hawkins_pooled_sequences.fastq

@seq13534-419
GCAGTAGCGGTCATAAGTGGTACATTACGAGATTCGGAGTACCATAGATTCGCATGAATCCCTGTGGATACGAGAGTGTGAGATATATGTACGCCAATCCAGTGTGATACCCATGAGATTTAGGACCGATGATGGTTGAGGACCAAGGATTGACCCGATGGATGCAGATTTGACCCCAGATAGAATAAATGCGATGAGATGATTTGGCCGATAGATAGATAGTGTCGTGAGGTGACGTCCGTCACTGGACGAA
+
IIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIDIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIFFFFDFFDFFDDFDFDFFFFDDFFDDFDDFF
@seq86249-867
GGATTAGCGGTCATAAGTCGTACATTACGAGATTCGGAGTACCATAGATTCGCATGAATCCCTGTGGATACGAGAGTGTGAGATATATGTACGCCAATCCAGTGTGATACCCATGAGATTTAGGACCGATGATGGTTGAGGACCAAGGATTGACCCGATGGATGCAGATTTGACCCCAGATAGAATAAATGCGATGAGATGATTTGGCCGATAGATAGATAGAGGTCAGTATAACCTCTCAAAGCTTTATCTACGGATGGATCCGCGC
+
IIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIDIIIIIIIIIIIIIIIIIIIIIIIIIIIIIII

In [16]:
%%bash

cat harrington_clinical_data.txt

Name	Color	Barcode
Abbey	Black	GCAGA
Adelaide	Orange	CTTGA
Alana	Black	AGCTA
Arabella	Black	TTGAG
Arianna	Orange	TCCGC
Bobby	Black	CCCAC
Brayden	Black	GCAGT
Bridget	Orange	CGGTT
Bruce	Orange	ACGGA
Byron	Orange	AGCGA
Cali	Orange	TTTTT
Camilla	Orange	ACAGG
Case	Black	GGGAT
Cason	Black	AACTG
Damien	Black	TGCAA
Dania	Black	CATCC
Dereon	Orange	ACACT
Destiney	Orange	CCGTG
Dominik	Black	GGATT
Gabrielle	Orange	CGAAG
Giancarlo	Orange	TATGG
Greta	Black	CCAAC
Israel	Orange	CCTTT
Javion	Orange	TAGCT
Jaylen	Black	TCCGG
Jazlyn	Yellow	AGTGA
Jordyn	Black	CCACC
Jordyna	Yellow	CATAT
Joshua	Black	TACGT
Justus	Black	GTTCA
Kamden	Orange	CCGTA
Karlee	Yellow	GTCGT
Kayla	Yellow	CATAA
Keaton	Green	GCTAA
Kian	Green	GGAAG
Kirsten	Black	TGTGA
Libby	Yellow	AGTCA
Lorelei	Orange	GCGGA
Mariela	Yellow	CGGAG
Martin	Green	CAATT
Mckayla	Green	AGAGT
Mckenzie	Black	GAAAA
Natalia	Green	GATTC
Santiago	Orange	TGTAT
Sarai	Black	CTAGT
Serena	Green	GGTAA
Shelby	Yellow	AAATG
Sienna	Green	GACCT
Terry	Orange	AACCC
Tristian	Black	TG

### getMutations.py

pysam needs python 3.6 downgrading from 3.8 now

In [13]:
%%writefile getMutations.py
import pysam

#This is a slightly modified version from here: https://pysam.readthedocs.io/en/latest/api.html
# What is a pileup? It is "piling up" all the reads that have mapped to a given position of your reference.
# It is a useful way to see what reads have a mutation and what don't. 

def pileup():
    #test file, replaced with the sorted.bam you are using. Make sure it is indexed! 
    #(Use samtools index yourbam.sorted.bam)
    samfile = pysam.AlignmentFile("/home/rbif/week6/necessary_scripts/faker.sorted.bam", "rb")

    #Since our reference only has a single sequence, we're going to pile up ALL of the reads. 
    #Usually you would do it in a specific region (such as chromosome 1, position 1023 to 1050 for example)
    for pileupcolumn in samfile.pileup():
        print ("coverage at base %s = %s" % (pileupcolumn.pos, pileupcolumn.n))
        #use a dictionary to count up the bases at each position
        ntdict = {}
        for pileupread in pileupcolumn.pileups:
            if not pileupread.is_del and not pileupread.is_refskip:
                # You can uncomment the below line to see what is happening in the pileup. 
                # print ('\tbase in read %s = %s' % (pileupread.alignment.query_name, pileupread.alignment.query_sequence[pileupread.query_position]))
                base = pileupread.alignment.query_sequence[pileupread.query_position]
                
                ########## ADD ADDITIONAL CODE HERE ############# 
                # Populate the ntdict with the counts of each base 
                # This dictionary will hold all of the base read counts per nucletoide per position.
                # Use the dictionary to calculate the frequency of each site, and report it if if the frequency is NOT  100% / 0%. 
                #############################################
        print (ntdict)
    samfile.close()

if __name__=="__main__":
    pileup()

Writing getMutations.py


### parseFastq.py

In [24]:
%%writefile parseFastq.py

import argparse
#Example use is 
# python parseFastq.py --fastq /home/rbif/week6/hawkins_pooled_sequences.fastq


################################################
# You can use this code and put it in your own script
class ParseFastQ(object):
    """Returns a read-by-read fastQ parser analogous to file.readline()"""
    def __init__(self,filePath,headerSymbols=['@','+']):
        """Returns a read-by-read fastQ parser analogous to file.readline().
        Exmpl: parser.next()
        -OR-
        Its an iterator so you can do:
        for rec in parser:
            ... do something with rec ...
 
        rec is tuple: (seqHeader,seqStr,qualHeader,qualStr)
        """
        if filePath.endswith('.gz'):
            self._file = gzip.open(filePath)
        else:
            self._file = open(filePath, 'rU')
        self._currentLineNumber = 0
        self._hdSyms = headerSymbols
         
    def __iter__(self):
        return self
    
    # I think this is supposed to be __next__(), so I'm changing it
    def __next__(self):
        """Reads in next element, parses, and does minimal verification.
        Returns: tuple: (seqHeader,seqStr,qualHeader,qualStr)"""
        # ++++ Get Next Four Lines ++++
        elemList = []
        for i in range(4):
            line = self._file.readline()
            self._currentLineNumber += 1 ## increment file position
            if line:
                elemList.append(line.strip('\n'))
            else: 
                elemList.append(None)
         
        # ++++ Check Lines For Expected Form ++++
        trues = [bool(x) for x in elemList].count(True)
        nones = elemList.count(None)
        # -- Check for acceptable end of file --
        if nones == 4:
            raise StopIteration
        # -- Make sure we got 4 full lines of data --
        assert trues == 4,\
               "** ERROR: It looks like I encountered a premature EOF or empty line.\n\
               Please check FastQ file near line number %s (plus or minus ~4 lines) and try again**" % (self._currentLineNumber)
        # -- Make sure we are in the correct "register" --
        assert elemList[0].startswith(self._hdSyms[0]),\
               "** ERROR: The 1st line in fastq element does not start with '%s'.\n\
               Please check FastQ file near line number %s (plus or minus ~4 lines) and try again**" % (self._hdSyms[0],self._currentLineNumber) 
        assert elemList[2].startswith(self._hdSyms[1]),\
               "** ERROR: The 3rd line in fastq element does not start with '%s'.\n\
               Please check FastQ file near line number %s (plus or minus ~4 lines) and try again**" % (self._hdSyms[1],self._currentLineNumber) 
        # -- Make sure the seq line and qual line have equal lengths --
        assert len(elemList[1]) == len(elemList[3]), "** ERROR: The length of Sequence data and Quality data of the last record aren't equal.\n\
               Please check FastQ file near line number %s (plus or minus ~4 lines) and try again**" % (self._currentLineNumber) 
         
        # ++++ Return fatsQ data as tuple ++++
        return tuple(elemList)
##########################################################################



if __name__ == "__main__":
    parser = argparse.ArgumentParser()
    parser.add_argument("-f", "--fastq", required=True, help="Place fastq inside here")
    args = parser.parse_args()

    #This is an example of how to use the function in your own code
    
    fastqfile = ParseFastQ(args.fastq)

    #A fastq read contains 4 lines
    for fastq_obj in fastqfile:
        #This fastq_obj is a tuple that has length of 4 and corresponds to those 4 lines
        #This is the header
        print(fastq_obj[0])
        #This is the sequence
        print(fastq_obj[1])
        #This is the separator
        print(fastq_obj[2])
        #This is the quality score
        print(fastq_obj[3])
        
        #Just an indicator showing the fastq "blocks"
        print('*'*10 + '==='*10 + '*' * 10)

Overwriting parseFastq.py


In [25]:
%%bash 

python parseFastq.py --fastq /home/rbif/week6/hawkins_pooled_sequences.fastq

IOPub data rate exceeded.
The notebook server will temporarily stop sending output
to the client in order to avoid crashing it.
To change this limit, set the config variable
`--NotebookApp.iopub_data_rate_limit`.

Current values:
NotebookApp.iopub_data_rate_limit=1000000.0 (bytes/sec)
NotebookApp.rate_limit_window=3.0 (secs)



hmmm....this must be a really big output, let me see if I can implement this in a code

## Workflow outline

Important note: We will not be able to use anything from BioPython for this assignment

### Demultiplex the pooled fastq by barcode

Create a single python script that:
1. Reads in the pooled fastq*
2. Uses the barcode from clinical data to find matches
3. Write to file
4. Trims barcode from start
5. Trims consequtive D or F from quality scores.
6. Set in foder with {name}_trimmed.fastq

### Dictionary Coding Structure

I will be using dictionarys to carry a lot of the heavy lifting inside this code. For example, I will be setting a coding_dict to make sure that everything is set in the right direction. Thus this will be more of a vinilla python programming exercise. 

In [94]:
with open("/home/rbif/week6/harrington_clinical_data.txt") as fin:
    rows = (line.split('\t') for line in fin )
    coding_dict = {row[1:][1].rstrip():{"name":row[0], "color":row[1]}  for row in rows}
    
coding_dict["GCAGT"]

{'name': 'Brayden', 'color': 'Black'}

### Parsing the Parser

In [95]:
from parseFastq import ParseFastQ

fastqfile = ParseFastQ("/home/rbif/week6/hawkins_pooled_sequences.fastq")
for item in fastqfile:
    #It seems like item[2] are all "+", let's just check that really quick 
    if item[2] != "+": print(item[2])

Item's 0, 1, and 3 are important to the work, so we will keep them in a dictionary.

In [96]:
fastqfile = ParseFastQ("/home/rbif/week6/hawkins_pooled_sequences.fastq")
fast_dict = {}

for item in fastqfile:
    fast_dict[item[0]] = {"tag":item[1][0:5], 
                          "seq":item[1][5:], 
                          "quality":item[3], 
                          "name":item[0]}

fast_dict['@seq13534-419']['tag']

'GCAGT'

In [99]:
report_dict = {}

for tag in coding_dict:
    if tag != 'Barcode':
        report_dict[tag] = {}

In [101]:
report_dict['GCAGT']

{}

### Merging Dictionarys 

Now we need to get these dictionarys into one final format. It would probably be best if I put these by name, but names can repeat, but I assume they would not repeat the tag. 

In [87]:
report_dict = {}

for tag in coding_dict:
    if tag != 'Barcode':
        report_dict[code] = {}

for item in fast_dict:
    # Not the most elegant solution, will recode if I have time.
    tag = fast_dict[item]["tag"]
    quality = fast_dict[item]["quality"]
    seq = fast_dict[item]["seq"]
    
    print(tag, item, coding_dict[tag]["name"], coding_dict[tag]["color"])
    
    report_dict[tag][item] = {item}

GCAGT @seq13534-419 Brayden Black
GGATT @seq86249-867 Dominik Black
GACCT @seq46647-928 Sienna Green
TTGAG @seq10275-134 Arabella Black
GTCGT @seq40495-618 Karlee Yellow
CTAGT @seq96545-592 Sarai Black
CGGAG @seq32226-291 Mariela Yellow
GCTAA @seq44244-909 Keaton Green
CGGAG @seq30148-814 Mariela Yellow
TGTAT @seq24027-303 Santiago Orange
TGTGA @seq69525-368 Kirsten Black
GACCT @seq89156-175 Sienna Green
CCACC @seq47485-551 Jordyn Black
AAATG @seq10758-496 Shelby Yellow
CCGTG @seq46720-763 Destiney Orange
GAAAA @seq67824-276 Mckenzie Black
TGACG @seq61428-359 Tristian Black
CAATT @seq19461-510 Martin Green
GCAGA @seq72638-854 Abbey Black
AACCC @seq67185-183 Terry Orange
CATCC @seq75999-675 Dania Black
CTTGA @seq53851-804 Adelaide Orange
AGCGA @seq44662-816 Byron Orange
TATGG @seq85042-305 Giancarlo Orange
GCAGT @seq42013-239 Brayden Black
ACGGA @seq48152-589 Bruce Orange
TCCGC @seq18886-982 Arianna Orange
CCCAC @seq28201-733 Bobby Black
GCGGA @seq60790-306 Lorelei Orange
ACGGA @seq7155

AAATG @seq45527-929 Shelby Yellow
AGAGT @seq98041-216 Mckayla Green
ACAGG @seq72074-934 Camilla Orange
GGATT @seq14705-885 Dominik Black
TGTGA @seq95268-653 Kirsten Black
TTGAG @seq18108-485 Arabella Black
CATAA @seq78357-150 Kayla Yellow
CTAGT @seq36912-836 Sarai Black
AGTCA @seq56540-987 Libby Yellow
GCGGA @seq71783-806 Lorelei Orange
AGCTA @seq86423-913 Alana Black
AGCTA @seq94799-250 Alana Black
GCGGA @seq19304-722 Lorelei Orange
GACCT @seq31916-128 Sienna Green
GCAGA @seq88230-810 Abbey Black
CATCC @seq42946-906 Dania Black
AACTG @seq18439-616 Cason Black
ACGGA @seq88325-304 Bruce Orange
AACCC @seq64400-116 Terry Orange
GACCT @seq15666-232 Sienna Green
GTCGT @seq95825-929 Karlee Yellow
GCAGT @seq36980-237 Brayden Black
GTTCA @seq91997-660 Justus Black
GTCGT @seq43683-891 Karlee Yellow
GACCT @seq44052-433 Sienna Green
GGTAA @seq54196-839 Serena Green
AAATG @seq17249-638 Shelby Yellow
GCAGA @seq19790-554 Abbey Black
AACCC @seq22375-240 Terry Orange
CTAGT @seq29592-683 Sarai Black
GT

TTGAG @seq93299-514 Arabella Black
GGAAG @seq58507-603 Kian Green
CATAT @seq49806-798 Jordyna Yellow
GCAGA @seq59473-468 Abbey Black
AGCTA @seq30751-712 Alana Black
GATTC @seq44068-247 Natalia Green
GGTAA @seq40736-959 Serena Green
GGGAT @seq34098-349 Case Black
CCACC @seq32741-906 Jordyn Black
ACGGA @seq79412-356 Bruce Orange
TATGG @seq15364-222 Giancarlo Orange
CTAGT @seq77892-626 Sarai Black
TAGCT @seq44516-773 Javion Orange
GGTAA @seq16347-221 Serena Green
CTTGA @seq63293-516 Adelaide Orange
GGAAG @seq42666-946 Kian Green
AACTG @seq69690-492 Cason Black
TCCGG @seq59980-536 Jaylen Black
AGTGA @seq93481-562 Jazlyn Yellow
TACGT @seq55359-393 Joshua Black
GGAAG @seq13901-579 Kian Green
AGAGT @seq70832-736 Mckayla Green
TACGT @seq76908-375 Joshua Black
CATAT @seq96222-766 Jordyna Yellow
TGACG @seq99144-666 Tristian Black
CTTGA @seq77729-321 Adelaide Orange
AGCTA @seq62904-641 Alana Black
GCAGA @seq57735-634 Abbey Black
GCTAA @seq61081-315 Keaton Green
GTTCA @seq24410-562 Justus Black
CC

AACCC @seq10653-409 Terry Orange
ACACT @seq69742-674 Dereon Orange
TGTAT @seq95449-921 Santiago Orange
CCTTT @seq77809-696 Israel Orange
CTAGT @seq82027-331 Sarai Black
CCTTT @seq70794-850 Israel Orange
TGCAA @seq15137-524 Damien Black
CCGTA @seq11975-803 Kamden Orange
CCTTT @seq41937-195 Israel Orange
TGCAA @seq48170-959 Damien Black
GATTC @seq91595-480 Natalia Green
GCAGA @seq95807-887 Abbey Black
ACGGA @seq45695-336 Bruce Orange
CCACC @seq49489-104 Jordyn Black
CCACC @seq52953-796 Jordyn Black
CGGTT @seq21619-421 Bridget Orange
AGTCA @seq45367-972 Libby Yellow
CCCAC @seq41450-999 Bobby Black
GATTC @seq76355-431 Natalia Green
GACCT @seq47739-351 Sienna Green
GCAGA @seq68632-746 Abbey Black
CGGTT @seq87969-784 Bridget Orange
GTTCA @seq15752-417 Justus Black
CCGTA @seq11606-999 Kamden Orange
AGCGA @seq11749-139 Byron Orange
GAAAA @seq22498-861 Mckenzie Black
GTTCA @seq23914-482 Justus Black
AGCGA @seq76886-432 Byron Orange
GACCT @seq71021-383 Sienna Green
GACCT @seq57980-827 Sienna Gre

AGTGA @seq89603-766 Jazlyn Yellow
GGTAA @seq22689-870 Serena Green
TGCAA @seq51911-646 Damien Black
AAATG @seq33808-292 Shelby Yellow
GAAAA @seq37931-185 Mckenzie Black
CATAA @seq93873-153 Kayla Yellow
GCAGT @seq52576-471 Brayden Black
CCCAC @seq21131-580 Bobby Black
AACTG @seq46377-460 Cason Black
GGATT @seq28687-504 Dominik Black
CCACC @seq54176-745 Jordyn Black
GCAGA @seq66487-549 Abbey Black
ACAGG @seq74575-456 Camilla Orange
AGCTA @seq88256-503 Alana Black
AGTGA @seq32540-560 Jazlyn Yellow
TTTTT @seq49645-835 Cali Orange
CCCAC @seq69750-389 Bobby Black
CATAT @seq38193-128 Jordyna Yellow
ACGGA @seq93364-557 Bruce Orange
ACAGG @seq28768-809 Camilla Orange
CATCC @seq32001-145 Dania Black
GGGAT @seq19768-783 Case Black
AACCC @seq20808-741 Terry Orange
CTTGA @seq16027-577 Adelaide Orange
CCTTT @seq87124-130 Israel Orange
TATGG @seq43732-655 Giancarlo Orange
GGATT @seq26830-908 Dominik Black
GCAGA @seq90351-485 Abbey Black
CATAA @seq24400-427 Kayla Yellow
TGTAT @seq46209-815 Santiago Or

...

TTTTT @seq87321-836 Cali Orange
CAATT @seq79958-715 Martin Green
TGCAA @seq96184-656 Damien Black
AACCC @seq76196-171 Terry Orange
TGTGA @seq37832-609 Kirsten Black
CAATT @seq71549-219 Martin Green
CTAGT @seq40749-116 Sarai Black
GACCT @seq57102-261 Sienna Green
AGAGT @seq44132-837 Mckayla Green
AAATG @seq89180-765 Shelby Yellow
GTCGT @seq85999-272 Karlee Yellow
TGCAA @seq75641-429 Damien Black
CCAAC @seq89470-121 Greta Black
TACGT @seq53789-718 Joshua Black
GGATT @seq10481-963 Dominik Black
CCGTG @seq49070-789 Destiney Orange
CAATT @seq26817-994 Martin Green
CCGTG @seq34883-947 Destiney Orange
AAATG @seq84618-757 Shelby Yellow
AAATG @seq26845-120 Shelby Yellow
GGGAT @seq82027-534 Case Black
AGCTA @seq89348-977 Alana Black
CCGTA @seq92018-404 Kamden Orange
CCGTA @seq54388-464 Kamden Orange
AAATG @seq25024-293 Shelby Yellow
GTTCA @seq75552-319 Justus Black
AAATG @seq50013-758 Shelby Yellow
AGCGA @seq28313-389 Byron Orange
GATTC @seq34412-979 Natalia Green
GTCGT @seq53827-438 Karlee Yell

GGAAG @seq14667-414 Kian Green
GGATT @seq27257-578 Dominik Black
CGGAG @seq26256-264 Mariela Yellow
AGAGT @seq64150-672 Mckayla Green
TTGAG @seq86227-297 Arabella Black
ACGGA @seq15502-771 Bruce Orange
AGAGT @seq59182-112 Mckayla Green
GGAAG @seq94055-571 Kian Green
CATCC @seq17636-675 Dania Black
CCACC @seq37039-989 Jordyn Black
GCTAA @seq34696-143 Keaton Green
CCGTG @seq48241-150 Destiney Orange
TTGAG @seq18691-808 Arabella Black
TGACG @seq25568-715 Tristian Black
TACGT @seq62463-149 Joshua Black
AGAGT @seq28222-712 Mckayla Green
GATTC @seq75791-158 Natalia Green
GTTCA @seq41337-298 Justus Black
ACAGG @seq45443-442 Camilla Orange
AGTCA @seq20543-786 Libby Yellow
AAATG @seq90567-844 Shelby Yellow
GGTAA @seq55546-279 Serena Green
GGAAG @seq66437-849 Kian Green
TTGAG @seq15637-517 Arabella Black
GACCT @seq54640-745 Sienna Green
AGAGT @seq32419-578 Mckayla Green
CATCC @seq21860-348 Dania Black
AGCTA @seq59934-636 Alana Black
TGTGA @seq38903-182 Kirsten Black
ACGGA @seq65451-458 Bruce Ora

CATAA @seq72581-527 Kayla Yellow
TTGAG @seq23313-994 Arabella Black
CATAA @seq52225-191 Kayla Yellow
GTCGT @seq43522-844 Karlee Yellow
CCGTA @seq96476-694 Kamden Orange
GGTAA @seq79255-783 Serena Green
AGCTA @seq96799-833 Alana Black
TATGG @seq38067-173 Giancarlo Orange
GTCGT @seq70940-370 Karlee Yellow
AGTGA @seq59063-417 Jazlyn Yellow
GGTAA @seq83515-665 Serena Green
GCAGA @seq22732-381 Abbey Black
TACGT @seq23255-501 Joshua Black
GCAGT @seq30224-860 Brayden Black
GTCGT @seq42243-294 Karlee Yellow
CATCC @seq30306-422 Dania Black
CTTGA @seq12899-211 Adelaide Orange
CATCC @seq24338-779 Dania Black
CGGAG @seq92522-694 Mariela Yellow
CGGAG @seq65178-785 Mariela Yellow
AACCC @seq30820-167 Terry Orange
AACCC @seq31252-296 Terry Orange
AAATG @seq16888-265 Shelby Yellow
ACACT @seq30570-385 Dereon Orange
TGTAT @seq68473-512 Santiago Orange
CGGTT @seq53381-431 Bridget Orange
CAATT @seq64611-992 Martin Green
GATTC @seq41055-460 Natalia Green
AACTG @seq14883-414 Cason Black
GGGAT @seq41389-298 C

GTTCA @seq75529-410 Justus Black
AAATG @seq67297-854 Shelby Yellow
GCAGT @seq76683-617 Brayden Black
AACCC @seq66353-159 Terry Orange
AACTG @seq48307-628 Cason Black
TGCAA @seq70261-298 Damien Black
GCGGA @seq34228-120 Lorelei Orange
CGAAG @seq83876-260 Gabrielle Orange
GAAAA @seq29924-102 Mckenzie Black
TTGAG @seq25717-660 Arabella Black
GCAGA @seq14804-685 Abbey Black
TGACG @seq66896-189 Tristian Black
AAATG @seq25034-461 Shelby Yellow
GCTAA @seq71581-501 Keaton Green
TGCAA @seq78361-801 Damien Black
GCAGA @seq60246-448 Abbey Black
GATTC @seq53928-432 Natalia Green
GCGGA @seq21463-933 Lorelei Orange
TTTTT @seq36699-360 Cali Orange
CCAAC @seq94135-725 Greta Black
AACTG @seq75780-963 Cason Black
CGAAG @seq13383-352 Gabrielle Orange
ACGGA @seq87012-991 Bruce Orange
CCGTG @seq53049-959 Destiney Orange
ACAGG @seq31338-515 Camilla Orange
TCCGC @seq32697-369 Arianna Orange
AGCGA @seq58449-681 Byron Orange
TCCGC @seq64304-167 Arianna Orange
AGCTA @seq23934-357 Alana Black
AGCGA @seq11211-227

TATGG @seq60501-439 Giancarlo Orange
CAATT @seq69509-284 Martin Green
CGGTT @seq23843-524 Bridget Orange
CGGTT @seq43703-593 Bridget Orange
GGATT @seq56599-671 Dominik Black
TGACG @seq46617-236 Tristian Black
AACCC @seq52567-426 Terry Orange
CTTGA @seq24252-754 Adelaide Orange
AAATG @seq76412-804 Shelby Yellow
CTAGT @seq27574-376 Sarai Black
AAATG @seq55981-374 Shelby Yellow
TACGT @seq89787-308 Joshua Black
AGTGA @seq65230-874 Jazlyn Yellow
AGTCA @seq24659-163 Libby Yellow
TGTGA @seq32920-458 Kirsten Black
GGAAG @seq72023-717 Kian Green
TGCAA @seq38598-634 Damien Black
GAAAA @seq46330-160 Mckenzie Black
AGAGT @seq39675-376 Mckayla Green
GATTC @seq55050-102 Natalia Green
GCGGA @seq88810-253 Lorelei Orange
AGAGT @seq95302-311 Mckayla Green
GATTC @seq34076-999 Natalia Green
TGCAA @seq92119-265 Damien Black
GGAAG @seq14271-659 Kian Green
TGTAT @seq90824-389 Santiago Orange
TACGT @seq47332-241 Joshua Black
CCTTT @seq84821-645 Israel Orange
AGTGA @seq75222-520 Jazlyn Yellow
GCTAA @seq55791-8

In [102]:
report_dict

{'GCAGA': {},
 'CTTGA': {},
 'AGCTA': {},
 'TTGAG': {},
 'TCCGC': {},
 'CCCAC': {},
 'GCAGT': {},
 'CGGTT': {},
 'ACGGA': {},
 'AGCGA': {},
 'TTTTT': {},
 'ACAGG': {},
 'GGGAT': {},
 'AACTG': {},
 'TGCAA': {},
 'CATCC': {},
 'ACACT': {},
 'CCGTG': {},
 'GGATT': {},
 'CGAAG': {},
 'TATGG': {},
 'CCAAC': {},
 'CCTTT': {},
 'TAGCT': {},
 'TCCGG': {},
 'AGTGA': {},
 'CCACC': {},
 'CATAT': {},
 'TACGT': {},
 'GTTCA': {},
 'CCGTA': {},
 'GTCGT': {},
 'CATAA': {},
 'GCTAA': {},
 'GGAAG': {},
 'TGTGA': {},
 'AGTCA': {},
 'GCGGA': {},
 'CGGAG': {},
 'CAATT': {},
 'AGAGT': {},
 'GAAAA': {},
 'GATTC': {},
 'TGTAT': {},
 'CTAGT': {},
 'GGTAA': {},
 'AAATG': {},
 'GACCT': {},
 'AACCC': {},
 'TGACG': {}}

In [29]:
#%%writefile pipeline.py
from parseFastq import ParseFastQ

class Main:
    def __init__(self):
        #First we are going to make a dictionary with all of the clinical entries
        with open("/home/rbif/week6/harrington_clinical_data.txt") as clinical:
            rows = (line.split('\t') for line in clinical)
            coding_dict = {row[1:][1].rstrip():{"name":row[0], "color":row[1]}  for row in rows}

        #Let's parse all of the fastqfile info into dictionary too
        fastqfile = ParseFastQ("/home/rbif/week6/hawkins_pooled_sequences.fastq")
        for i in fastqfile:
            print(i[0],i[1],i[2],i[3])
            print("hello!")
        
    def trimmer(self):
        pass
    
if __name__== "__main__":    
    Main()

@seq13534-419 GCAGTAGCGGTCATAAGTGGTACATTACGAGATTCGGAGTACCATAGATTCGCATGAATCCCTGTGGATACGAGAGTGTGAGATATATGTACGCCAATCCAGTGTGATACCCATGAGATTTAGGACCGATGATGGTTGAGGACCAAGGATTGACCCGATGGATGCAGATTTGACCCCAGATAGAATAAATGCGATGAGATGATTTGGCCGATAGATAGATAGTGTCGTGAGGTGACGTCCGTCACTGGACGAA + IIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIDIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIFFFFDFFDFFDDFDFDFFFFDDFFDDFDDFF
hello!
@seq86249-867 GGATTAGCGGTCATAAGTCGTACATTACGAGATTCGGAGTACCATAGATTCGCATGAATCCCTGTGGATACGAGAGTGTGAGATATATGTACGCCAATCCAGTGTGATACCCATGAGATTTAGGACCGATGATGGTTGAGGACCAAGGATTGACCCGATGGATGCAGATTTGACCCCAGATAGAATAAATGCGATGAGATGATTTGGCCGATAGATAGATAGAGGTCAGTATAACCTCTCAAAGCTTTATCTACGGATGGATCCGCGC + IIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIDIIIIIIIIIIIIIIIIIIIIIIII

@seq60460-854 CCGTGAGCGGTCATAAGTGGTACATTACGAGATTCGGAGTACCATAGATTCGCATGAATCCCTGTGGATACGAGAGTGTGAGATATATCTACGCCAATCCAGTGTGATACCCATGAGATTTAGGACCGATGATGGTTGAGGACCAAGGATTGACCCGATGGATGCAGATTTGACCCCAGATAGAATAAATGCGATGAGATGATTTGGCCGATAGATAGATAGGTGGATATCCGCACATGTGATTATTGTGGGC + IIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIFIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIDDFDFDFFFDDDFFFDDFFDFDDFDFDDFDF
hello!
@seq32649-216 CAATTAGCGGTCATAAGTGGTACATTACGAGATTCGGAGTACCATAGATTCGCATGAATCCCTGTGGATACGAGAGTGTGAGATATATGTACGCCAATCCAGTGTGATACCCATGAGATTTAGGACCGATGATGGTTGAGGACCAAGGATTGACCCGATGGATGCAGATTTGACCCCAGATAGAATAAATGCGATGAGATGATTTGGCCGATAGATAGATAGCTACAAACGGGGTCGTAACATTAAATCACTTCCGACATACCTC + IIIIIIIIIIIFIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIII

@seq80118-690 CTTGAAGCGGTCATAAGTGGTACATTACGAGATTCGGAGTACCATAGATTCGCATGAATCCCTGTGGATACGAGAGTGTGAGATATATGTACGCCAATCCAGTGTGATACCCATGAGATTTAGGACCGATGATGGTTGAGGACCAAGGATTGACCCGATGGATGCAGATTTGACCCCAGATAGAATAAATGCGATGAGATGATTTGGCCGATAGATAGATAGCCGATGTTAATGTCACCGCTCTAATGAGGGGTTAGCCTTTAGAGA + IIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIDIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIDFFDFDDDFFFFFDDDFDDFDFDFFFDDDDFDFDDDFFDDFDDFF
hello!
@seq37129-788 GAAAAAGCGGTCATAAGTCGTACATTACGAGATTCGGAGTACCATAGATTCGCATGAATCCCTGTGGATACGAGAGTGTGAGATATATGTACGCCAATCCAGTGTGATACCCATGAGATTTAGGACCGATGATGGTTGAGGACCAAGGATTGACCCGATGGATGCAGATTTGACCCCAGATAGAATAAATGCGATGAGATGATTTGGCCGATAGATAGATAGGAACCTTTATACCGGTTTTATCGTAACACATGTGGA + IIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIFIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIII

@seq22879-268 TGCAAAGCGGTCATAAGTCGTACATTACGAGATTCGGAGTACCATAGATTCGCATGAATCCCTGTGGATACGAGAGTGTGAGATATATGTACGCCAATCCAGTGTGATACCCATGAGATTTAGGACCGATGATGGTTGAGGACCAAGGATTGACCCGATGGATGCAGATTTGACCCCAGATAGAATAAATGCGATGAGATGATTTGGCCGATAGATAGATAGGTCTAGTGTGAGTGATGGATTGGTTGGCAACCGTATACGCAATCAT + IIIIIIIIIIIIIDIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIFDDDDFDFFFDFDDFDFDFFFFDFDDDFDFFFDFDFDFFFFDFDDF
hello!
@seq26750-360 CCTTTAGCGGTCATAAGTGGTACATTACGAGATTCGGAGTACCATAGATTCGCATGAATCCCTGTGGATACGAGAGTGTGAGATATATGTACGCCAATCCAGTGTGATACCCATGAGATTTAGGACCGATGATGGTTGAGGACCAAGGATTGACCCGATGGATGCAGATTTGACCCCAGATAGAATAAATGCGATGAGATGATTTGGCCGATAGATAGATAGGGCTGAGCACCACCAACAT + IIIIIIIIIIIIIIIIIIIIIFIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIII

hello!
@seq10653-409 AACCCAGCGGTCATAAGTGGTACATTACGAGATTCGGAGTACCATAGATTCGCATGAATCCCTGTGGATACGAGAGTGTGAGATATATGTACGCCAATCCAGTGTGATACCCATGAGATTTAGGACCGATGATGGTTGAGGACCAAGGATTGACCCGATGGATGCAGATTTGACCCCAGATAGAATAAATGCGATGAGATGATTTGGCCGATAGATAGATAGTCCCTGTGTTACGGACACAAAAAACAG + IIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIFIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIDDFFFFDDDFFDDFDDDFFFDFDFDDD
hello!
@seq69742-674 ACACTAGCGGTCATAAGTGGTACATTACGAGATTCGGAGTACCATAGATTCGCATGAATCCCTGTGGATACGAGAGTGTGAGATATATCTACGCCAATCCAGTGTGATACCCATGAGATTTAGGACCGATGATGGTTGAGGACCAAGGATTGACCCGATGGATGCAGATTTGACCCCAGATAGAATAAATGCGATGAGATGATTTGGCCGATAGATAGATAGGTATGTATCTATGAT + IIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIDIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIII

...

@seq60673-179 CATAAAGCGGTCATAAGTGGTACATTACGAGATTCGGAGTACCATAGATTCGCATGAATCCCTGTGGATACGAGAGTGTGAGATATATGTACGCCAATCCAGTGTGATACCCATGAGATTTAGGACCGATGATGGTTGAGGACCAAGGATTGACCCGATGGATGCAGATTTGACCCCAGATAGAATAAATGCGATGAGATGATTTGGCCGATAGATAGATAGACCCTATTGGCC + IIIIIIIIIIIIIIIIIIIIIIIIIDIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIFFFDFDDDDFDF
hello!
@seq75633-289 AGCGAAGCGGTCATAAGTGGTACATTACGAGATTCGGAGTACCATAGATTCGCATGAATCCCTGTGGATACGAGAGTGTGAGATATATGTACGCCAATCCAGTGTGATACCCATGAGATTTAGGACCGATGATGGTTGAGGACCAAGGATTGACCCGATGGATGCAGATTTGACCCCAGATAGAATAAATGCGATGAGATGATTTGGCCGATAGATAGATAGAGCGTGTGTACCCACATGCAAACGGTGGATGTTTGAGAACGCCCATTGTT + IIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIDIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIII

@seq55684-278 CTAGTAGCGGTCATAAGTCGTACATTACGAGATTCGGAGTACCATAGATTCGCATGAATCCCTGTGGATACGAGAGTGTGAGATATATGTACGCCAATCCAGTGTGATACCCATGAGATTTAGGACCGATGATGGTTGAGGACCAAGGATTGACCCGATGGATGCAGATTTGACCCCAGATAGAATAAATGCGATGAGATGATTTGGCCGATAGATAGATAGCGATACTTAGTGCCCTGGTGCACAAAGCACC + IIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIDIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIFDDDFDDDFFFFDFFFDDDDDFFFFFFFFDD
hello!
@seq34066-913 GGAAGAGCGGTCATAAGTGGTACATTACGAGATTCGGAGTACCATAGATTCGCATGAATCCCTGTGGATACGAGAGTGTGAGATATATGTACGCCAATCCAGTGTGATACCCATGAGATTTAGGACCGATGATGGTTGAGGACCAAGGATTGACCCGATGGATGCAGATTTGACCCCAGATAGAATAAATGCGATGAGATGATTTGGCCGATAGATAGATAGACAAAACATAGCTACTTGGAACATATC + IIIIIIIIIIFIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIII

@seq22864-964 GAAAAAGCGGTCATAAGTCGTACATTACGAGATTCGGAGTACCATAGATTCGCATGAATCCCTGTGGATACGAGAGTGTGAGATATATGTACGCCAATCCAGTGTGATACCCATGAGATTTAGGACCGATGATGGTTGAGGACCAAGGATTGACCCGATGGATGCAGATTTGACCCCAGATAGAATAAATGCGATGAGATGATTTGGCCGATAGATAGATAGGCGGCGATAGTTCTAGGTGTGGTGCTTCCCCATCCTTCGATAAGTT + IIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIFIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIDFFFDDFDFDDDFFDFFDDFDDDFDDFFFDDDDDFFDFFDDFDFDD
hello!
@seq89478-988 AGTCAAGCGGTCATAAGTGGTACATTACGAGATTCGGAGTACCATAGATTCGCATGAATCCCTGTGGATACGAGAGTGTGAGATATATGTACGCCAATCCAGTGTGATACCCATGAGATTTAGGACCGATGATGGTTGAGGACCAAGGATTGACCCGATGGATGCAGATTTGACCCCAGATAGAATAAATGCGATGAGATGATTTGGCCGATAGATAGATAGGCCCTTGTTTATTT + IIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIDIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIII

@seq77709-362 GCAGAAGCGGTCATAAGTCGTACATTACGAGATTCGGAGTACCATAGATTCGCATGAATCCCTGTGGATACGAGAGTGTGAGATATATGTACGCCAATCCAGTGTGATACCCATGAGATTTAGGACCGATGATGGTTGAGGACCAAGGATTGACCCGATGGATGCAGATTTGACCCCAGATAGAATAAATGCGATGAGATGATTTGGCCGATAGATAGATAGCGTTTTATAATGATGTAAAGGAATAGGGTTGT + IIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIDIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIDFDFFFDFDFDFFDDFDFDDDFDDFDDFFFFD
hello!
@seq75288-483 GGGATAGCGGTCATAAGTCGTACATTACGAGATTCGGAGTACCATAGATTCGCATGAATCCCTGTGGATACGAGAGTGTGAGATATATGTACGCCAATCCAGTGTGATACCCATGAGATTTAGGACCGATGATGGTTGAGGACCAAGGATTGACCCGATGGATGCAGATTTGACCCCAGATAGAATAAATGCGATGAGATGATTTGGCCGATAGATAGATAGGCACGGCACAGTTAAAC + IIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIDIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIII

IOPub data rate exceeded.
The notebook server will temporarily stop sending output
to the client in order to avoid crashing it.
To change this limit, set the config variable
`--NotebookApp.iopub_data_rate_limit`.

Current values:
NotebookApp.iopub_data_rate_limit=1000000.0 (bytes/sec)
NotebookApp.rate_limit_window=3.0 (secs)

